In [0]:
# ============================================
# CELL 1: Secure ADLS Access via Key Vault
# ============================================
storage_account_name = "adls31tejashree"
container_name       = "healthcare-project"

# Fetch secrets securely from Key Vault — no hardcoded keys!
storage_account_key = dbutils.secrets.get(
    scope="healthcare-kv-scope",
    key="adls-account-key"
)

# Accept parameters from ADF (with defaults for manual runs)
try:
    process_date = dbutils.widgets.get("p_process_date")
    container    = dbutils.widgets.get("p_container")
except:
    process_date = "20260213"
    container    = "healthcare-project"

spark.conf.set(
    f"fs.azure.account.key.{storage_account_name}.dfs.core.windows.net",
    storage_account_key
)

base_path   = f"abfss://{container}@{storage_account_name}.dfs.core.windows.net"
silver_path = f"{base_path}/silver/hospital_records/processed_{process_date}/"

print(f"✅ Secrets loaded from Key Vault")
print(f"✅ Process date: {process_date}")
print(f"✅ Silver path: {silver_path}")

✅ Secrets loaded from Key Vault
✅ Process date: 20260213
✅ Silver path: abfss://healthcare-project@adls31tejashree.dfs.core.windows.net/silver/hospital_records/processed_20260213/


In [0]:
# ============================================
# CELL 2: Read Silver Layer (Parquet)
# ============================================
silver_path = f"{base_path}/silver/hospital_records/processed_20260213/"

df_silver = spark.read.parquet(silver_path)
print(f"Total rows: {df_silver.count()}")
print(f"Schema:")
df_silver.printSchema()
df_silver.show(5)

Total rows: 55500
Schema:
root
 |-- Name: string (nullable = true)
 |-- Age: string (nullable = true)
 |-- Gender: string (nullable = true)
 |-- Blood_Type: string (nullable = true)
 |-- Medical_Condition: string (nullable = true)
 |-- Date_of_Admission: string (nullable = true)
 |-- Doctor: string (nullable = true)
 |-- Hospital: string (nullable = true)
 |-- Insurance_Provider: string (nullable = true)
 |-- Billing_Amount: string (nullable = true)
 |-- Room_Number: string (nullable = true)
 |-- Admission_Type: string (nullable = true)
 |-- Discharge_Date: string (nullable = true)
 |-- Medication: string (nullable = true)
 |-- Test_Results: string (nullable = true)

+-------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+
|         Name|Age|Gender|Blood_Type|Medical_Condition|Date_of_Admission|          Doctor|            Hospi

In [0]:
# ============================================
# CELL 3: Clean & Transform (Silver Layer)
# ============================================
from pyspark.sql.functions import col, to_date, datediff, round, upper, trim, when

df_clean = df_silver \
    .withColumn("Date_of_Admission", to_date(col("Date_of_Admission"), "yyyy-MM-dd")) \
    .withColumn("Discharge_Date",    to_date(col("Discharge_Date"),    "yyyy-MM-dd")) \
    .withColumn("Length_of_Stay",    datediff(col("Discharge_Date"), col("Date_of_Admission"))) \
    .withColumn("Billing_Amount",    round(col("Billing_Amount"), 2)) \
    .withColumn("Gender",            upper(trim(col("Gender")))) \
    .withColumn("Medical_Condition", upper(trim(col("Medical_Condition")))) \
    .withColumn("Admission_Type",    upper(trim(col("Admission_Type")))) \
    .withColumn("Test_Results",      upper(trim(col("Test_Results")))) \
    .dropDuplicates() \
    .filter(col("Billing_Amount") > 0) \
    .filter(col("Age").isNotNull())

print(f"Clean rows: {df_clean.count()}")
df_clean.display(5)

Clean rows: 54860


Name Age Gender Blood_Type Medical_Condition Date_of_Admission Doctor Hospital Insurance_Provider Billing_Amount Room_Number Admission_Type Discharge_Date Medication Test_Results Length_of_Stay ashlEY grAy 68 MALE A+ ASTHMA 2020-10-06 Lisa Payne and Weber Sons Aetna 41548.41 124 URGENT 2020-10-20 Aspirin NORMAL 14 JASmine sHort 40 FEMALE O- CANCER 2021-02-23 Amy Johnson Bailey-Hunt Medicare 8867.75 302 EMERGENCY 2021-03-20 Lipitor INCONCLUSIVE 25 vInCent RAY 56 MALE A- CANCER 2019-06-21 Robert Martinez Inc Swanson Blue Cross 30414.77 310 URGENT 2019-07-11 Ibuprofen ABNORMAL 20 liNda BUtler 23 FEMALE O+ DIABETES 2023-11-07 Michael Owens Sharp-Greer Medicare 11209.42 452 EMERGENCY 2023-12-05 Lipitor ABNORMAL 28 aMaNdA joHNsON 27 FEMALE O- ASTHMA 2024-02-17 Cindy Herrera Sons and Nguyen Blue Cross 34770.04 272 EMERGENCY 2024-03-06 Aspirin NORMAL 18 EliZABETh tYleR 42 MALE AB- OBESITY 2023-08-24 Mark Lee Macdonald Group Blue Cross 44356.3 166 URGENT 2023-09-12 Ibuprofen ABNORMAL 19 PAtRICk RODRiGUez 36 MALE O- DIABETES 2022-06-15 Mary King Woodard, and Martin Baker Aetna 36080.33 282 URGENT 2022-07-06 Penicillin ABNORMAL 21 RoBerT HuBbARD 69 MALE B- ASTHMA 2023-11-13 Heather Church Davis-Freeman Medicare 23031.25 431 URGENT 2023-11-23 Ibuprofen ABNORMAL 10 DANa pOttEr 49 FEMALE B+ HYPERTENSION 2022-06-14 Samuel Navarro Jones Ltd Cigna 9955.32 137 URGENT 2022-06-19 Paracetamol NORMAL 5 GeOrgE lArSen 72 FEMALE A- HYPERTENSION 2020-10-03 Juan Kelley Wilson and Thomas, Anderson Cigna 10023.49 361 ELECTIVE 2020-10-13 Ibuprofen ABNORMAL 10 teresA teRRy 43 MALE O+ HYPERTENSION 2019-07-01 Bob Lopez Ltd Wilkins Aetna 49980.48 367 ELECTIVE 2019-07-04 Penicillin ABNORMAL 3 HeAthEr DAvis 73 FEMALE A+ CANCER 2023-06-07 Steven Sutton Mendoza-Wilson Medicare 19391.54 466 ELECTIVE 2023-06-19 Penicillin ABNORMAL 12 sHERrY JaMEs 31 FEMALE B+ ASTHMA 2021-09-20 Sean Chambers Gilbert-Morales Blue Cross 30108.94 158 URGENT 2021-10-11 Lipitor NORMAL 21 roBERt VargAS 36 FEMALE O+ HYPERTENSION 2022-10-01 Ann Baldwin Glass-Taylor Blue Cross 13972.9 288 ELECTIVE 2022-10-16 Aspirin ABNORMAL 15 roBERT sTokEs 82 MALE A- ASTHMA 2023-03-21 James Palmer Jones-Hill Cigna 28518.6 165 ELECTIVE 2023-04-14 Paracetamol ABNORMAL 24 JEffREy ROBInSon 51 FEMALE A+ ASTHMA 2022-01-20 Andrea Gutierrez Russell and Moss Moreno, Aetna 43878.19 473 ELECTIVE 2022-01-31 Paracetamol ABNORMAL 11 tomMY farRELL 29 MALE O+ CANCER 2022-03-06 Penny Hill Weaver and Parks, Odom Blue Cross 20714.35 432 URGENT 2022-03-08 Lipitor ABNORMAL 2 mONIQUE ALExanDeR 64 FEMALE AB+ HYPERTENSION 2021-02-27 Hector Pena LLC Jones Medicare 29653.02 160 URGENT 2021-03-19 Penicillin INCONCLUSIVE 20 ricHARd trAN 63 FEMALE A+ CANCER 2023-12-02 Brandi Houston Palmer and Fisher Baker, UnitedHealthcare 21496.36 450 URGENT 2023-12-31 Paracetamol INCONCLUSIVE 29 Pamela BakeR 55 MALE O- ASTHMA 2020-02-21 Walter Leon Group Gonzales Blue Cross 31411.97 340 EMERGENCY 2020-03-16 Penicillin INCONCLUSIVE 24 cheryl StriCklAND 22 FEMALE B- HYPERTENSION 2020-04-09 Nichole Carney Moore Sons and Aetna 7183.8 377 URGENT 2020-04-25 Penicillin INCONCLUSIVE 16 aNgelA MUlLeN 70 MALE B- ARTHRITIS 2023-12-03 Scott Contreras Novak-Gutierrez UnitedHealthcare 30796.31 334 ELECTIVE 2023-12-11 Penicillin ABNORMAL 8 mIchele MCMIllAn 65 FEMALE A- HYPERTENSION 2024-04-23 Kelsey Davis Osborn-Park Aetna 39524.11 302 EMERGENCY 2024-05-15 Lipitor NORMAL 22 CArL McCARthY 72 FEMALE O- OBESITY 2019-09-13 Richard Booker Cochran Whitney, and Novak UnitedHealthcare 41808.53 102 ELECTIVE 2019-09-26 Aspirin INCONCLUSIVE 13 rAchel mArtinEz dvM 40 MALE AB+ HYPERTENSION 2021-12-24 Annette Schaefer and Webb Knapp Williams, Aetna 4439.68 133 ELECTIVE 2022-01-18 Lipitor INCONCLUSIVE 25 amanDA chERry 62 MALE A- OBESITY 2020-04-30 Jose Howell Mckinney-Vasquez Cigna 4521.27 424 EMERGENCY 2020-05-07 Lipitor NORMAL 7 jEssica nEwmAN 22 FEMALE O+ HYPERTENSION 2021-07-07 Rebecca Walker LLC Horton Blue Cross 25726.62 163 EMERGENCY 2021-07-10 Lipitor NORMAL 3 jeSSiCA fe

In [0]:
# ============================================
# CELL 4: GOLD - Readmission Rates by Condition
# ============================================
from pyspark.sql.functions import count, avg, sum as spark_sum

df_readmission = df_clean \
    .groupBy("Medical_Condition", "Admission_Type") \
    .agg(
        count("*").alias("Total_Admissions"),
        avg("Length_of_Stay").alias("Avg_Length_of_Stay"),
        avg("Billing_Amount").alias("Avg_Billing_Amount")
    ) \
    .withColumn("Avg_Length_of_Stay", round(col("Avg_Length_of_Stay"), 2)) \
    .withColumn("Avg_Billing_Amount", round(col("Avg_Billing_Amount"), 2)) \
    .orderBy(col("Total_Admissions").desc())

df_readmission.display(10)

# Write to Gold
df_readmission.write.mode("overwrite").parquet(
    f"{base_path}/gold/hospital_records/readmission_rates/"
)
print("✅ Gold: readmission_rates written!")

Medical_Condition Admission_Type Total_Admissions Avg_Length_of_Stay Avg_Billing_Amount DIABETES URGENT 3188 15.1 25557.7 HYPERTENSION ELECTIVE 3171 15.45 25645.31 CANCER ELECTIVE 3108 15.26 25722.77 OBESITY EMERGENCY 3092 15.49 25888.14 ARTHRITIS URGENT 3079 15.38 25592.37 ARTHRITIS EMERGENCY 3070 15.5 25522.33 ASTHMA ELECTIVE 3064 15.72 25296.41 ARTHRITIS ELECTIVE 3058 15.62 25513.74 ASTHMA URGENT 3040 15.75 25830.61 CANCER URGENT 3030 15.27 24967.75 DIABETES ELECTIVE 3027 15.62 26066.73 OBESITY URGENT 3026 15.44 25947.37 OBESITY ELECTIVE 3009 15.39 25740.84 HYPERTENSION URGENT 2990 15.5 25513.93 CANCER EMERGENCY 2983 16.02 24909.35 DIABETES EMERGENCY 2982 15.58 25524.05 ASTHMA EMERGENCY 2973 15.55 25937.77 HYPERTENSION EMERGENCY 2970 15.35 25514.82

✅ Gold: readmission_rates written!


In [0]:
# ============================================
# CELL 5: GOLD - Diagnosis Trends by Age Group
# ============================================
from pyspark.sql.functions import year

df_diagnosis = df_clean \
    .withColumn("Age_Group", 
        when(col("Age") < 18,  "0-17")
        .when(col("Age") < 35, "18-34")
        .when(col("Age") < 50, "35-49")
        .when(col("Age") < 65, "50-64")
        .otherwise("65+")
    ) \
    .withColumn("Admission_Year", year(col("Date_of_Admission"))) \
    .groupBy("Medical_Condition", "Age_Group", "Admission_Year") \
    .agg(
        count("*").alias("Case_Count"),
        avg("Billing_Amount").alias("Avg_Cost")
    ) \
    .withColumn("Avg_Cost", round(col("Avg_Cost"), 2)) \
    .orderBy(col("Case_Count").desc())

df_diagnosis.display(10)

# Write to Gold
df_diagnosis.write.mode("overwrite").parquet(
    f"{base_path}/gold/hospital_records/diagnosis_trends/"
)
print("✅ Gold: diagnosis_trends written!")

Medical_Condition Age_Group Admission_Year Case_Count Avg_Cost HYPERTENSION 65+ 2020 625 25044.99 CANCER 65+ 2020 597 23646.75 DIABETES 65+ 2022 587 25740.1 ASTHMA 65+ 2021 587 25696.6 ARTHRITIS 65+ 2022 583 26173.39 HYPERTENSION 65+ 2022 577 26094.4 HYPERTENSION 65+ 2021 575 26041.04 ARTHRITIS 65+ 2021 575 25845.13 ASTHMA 65+ 2020 574 26525.98 OBESITY 65+ 2020 567 25284.35 CANCER 65+ 2022 566 24721.47 CANCER 65+ 2023 561 25825.55 OBESITY 65+ 2023 559 25564.34 DIABETES 65+ 2023 557 26258.28 DIABETES 65+ 2021 556 26151.76 ARTHRITIS 65+ 2020 548 24501.3 ARTHRITIS 65+ 2023 547 26022.09 OBESITY 65+ 2021 545 25131.68 ASTHMA 65+ 2022 543 25339.97 HYPERTENSION 65+ 2023 539 25400.01 ASTHMA 65+ 2023 536 25715.52 OBESITY 65+ 2022 529 25765.65 DIABETES 65+ 2020 526 25758.36 CANCER 65+ 2021 509 24976.8 OBESITY 18-34 2023 494 26228.67 OBESITY 50-64 2020 479 25904.36 ARTHRITIS 18-34 2020 475 24700.47 DIABETES 50-64 2022 475 25197.63 CANCER 18-34 2020 473 25060.01 OBESITY 35-49 2020 472 25256.62 HYPERTENSION 18-34 2020 463 25247.53 CANCER 50-64 2020 457 26181.98 DIABETES 18-34 2023 457 24942.43 HYPERTENSION 18-34 2023 455 25807.03 CANCER 18-34 2023 453 25706.4 CANCER 18-34 2021 451 25150.35 ARTHRITIS 18-34 2022 447 25134.52 DIABETES 18-34 2021 447 25098.7 DIABETES 18-34 2022 447 26027.92 OBESITY 50-64 2021 446 25300.89 ARTHRITIS 18-34 2021 444 25756.94 OBESITY 18-34 2022 443 26694.06 HYPERTENSION 18-34 2021 442 25484.48 ASTHMA 18-34 2023 441 25260.77 ASTHMA 18-34 2022 441 25691.98 HYPERTENSION 18-34 2022 440 24980.3 DIABETES 35-49 2020 438 25496.44 OBESITY 18-34 2021 438 25561.07 ARTHRITIS 35-49 2020 437 25398.33 ASTHMA 18-34 2020 436 26638.05 HYPERTENSION 50-64 2021 431 26512.14 ARTHRITIS 35-49 2023 430 25351.23 ARTHRITIS 50-64 2022 429 26456.24 CANCER 35-49 2022 429 23137.1 CANCER 18-34 2022 429 24890.0 ASTHMA 18-34 2021 427 25965.36 OBESITY 18-34 2020 425 25522.55 DIABETES 18-34 2020 423 25859.88 HYPERTENSION 50-64 2023 422 26314.45 ARTHRITIS 18-34 2023 417 25830.59 CANCER 50-64 2023 416 26589.63 ARTHRITIS 35-49 2021 414 24430.38 DIABETES 35-49 2023 413 24931.16 ARTHRITIS 50-64 2023 411 25924.83 ASTHMA 35-49 2021 411 25718.19 HYPERTENSION 35-49 2023 408 25164.9 OBESITY 35-49 2022 408 25929.49 HYPERTENSION 50-64 2022 408 25907.22 ASTHMA 50-64 2023 407 24745.06 DIABETES 35-49 2022 407 25531.43 OBESITY 50-64 2023 406 26708.03 ASTHMA 65+ 2019 406 24979.41 DIABETES 50-64 2023 404 24700.73 ARTHRITIS 50-64 2020 403 24766.11 DIABETES 35-49 2021 402 26153.15 HYPERTENSION 50-64 2020 401 24487.96 DIABETES 50-64 2020 399 26486.91 ASTHMA 35-49 2020 396 25719.7 HYPERTENSION 35-49 2021 393 25383.48 HYPERTENSION 35-49 2022 392 25664.62 CANCER 35-49 2023 390 24000.02 DIABETES 65+ 2019 388 25534.25 ASTHMA 35-49 2023 388 25134.55 ASTHMA 50-64 2021 388 25491.42 HYPERTENSION 35-49 2020 386 26808.8 ARTHRITIS 50-64 2021 386 25976.04 CANCER 35-49 2021 385 26052.96 OBESITY 50-64 2022 385 25175.3 ASTHMA 50-64 2022 384 25519.89 OBESITY 35-49 2023 382 26187.75 ARTHRITIS 65+ 2019 381 25829.17 ASTHMA 35-49 2022 379 25382.59 CANCER 50-64 2021 378 25699.84 CANCER 50-64 2022 377 26330.67 CANCER 65+ 2019 377 24650.04 OBESITY 35-49 2021 377 26665.08 ASTHMA 50-64 2020 376 25583.99 DIABETES 50-64 2021 368 26113.76 ARTHRITIS 35-49 2022 366 26448.82 CANCER 35-49 2020 350 25540.74 OBESITY 65+ 2019 344 26327.87 HYPERTENSION 65+ 2019 335 25209.25 ASTHMA 18-34 2019 333 26434.87 OBESITY 18-34 2019 314 26440.79 CANCER 18-34 2019 308 25782.98 CANCER 35-49 2019 302 26675.99 ARTHRITIS 18-34 2019 296 24699.49 DIABETES 35-49 2019 288 26353.56 HYPERTENSION 18-34 2019 287 26007.74 HYPERTENSION 35-49 2019 284 25512.57 DIABETES 50-64 2019 283 27053.97 CANCER 50-64 2019 275 24454.3 ASTHMA 35-49 2019 273 27143.21 DIABETES 18-34 2019 269 25486.56 HYPERTENSION 50-64 2019 264 24100.77 ARTHRITIS 50-64 2019 264 25545.67 ASTHMA 50-64 2019 257 24515.46 OBESITY 50-64 2019 248 25193.55 OBESITY 35-49 2019 245 28696.3 ARTHRITIS 35-49 2019 244 25999.64 ASTHMA 65+ 2024 219 25173.4 ARTHRITIS 65+ 2024 214 26

✅ Gold: diagnosis_trends written!


In [0]:
# ============================================
# CELL 6: GOLD - Average Treatment Costs
# ============================================
df_costs = df_clean \
    .groupBy("Medical_Condition", "Medication", "Insurance_Provider") \
    .agg(
        count("*").alias("Patient_Count"),
        avg("Billing_Amount").alias("Avg_Treatment_Cost"),
        avg("Length_of_Stay").alias("Avg_Stay_Days")
    ) \
    .withColumn("Avg_Treatment_Cost", round(col("Avg_Treatment_Cost"), 2)) \
    .withColumn("Avg_Stay_Days",      round(col("Avg_Stay_Days"), 2)) \
    .orderBy(col("Avg_Treatment_Cost").desc())

df_costs.display(10)

# Write to Gold
df_costs.write.mode("overwrite").parquet(
    f"{base_path}/gold/hospital_records/avg_treatment_costs/"
)
print("✅ Gold: avg_treatment_costs written!")

Medical_Condition Medication Insurance_Provider Patient_Count Avg_Treatment_Cost Avg_Stay_Days DIABETES Paracetamol Aetna 358 28071.0 15.57 OBESITY Ibuprofen Cigna 366 27773.12 15.05 DIABETES Aspirin Medicare 387 27544.46 15.55 OBESITY Aspirin Blue Cross 387 27263.09 15.03 OBESITY Aspirin Cigna 397 26982.56 15.83 OBESITY Ibuprofen Medicare 366 26923.43 15.38 CANCER Lipitor Cigna 351 26837.21 14.53 ASTHMA Paracetamol Aetna 365 26822.52 15.15 HYPERTENSION Ibuprofen Blue Cross 360 26781.75 15.13 ARTHRITIS Aspirin UnitedHealthcare 397 26775.75 16.14 ASTHMA Aspirin UnitedHealthcare 328 26758.39 15.03 ASTHMA Ibuprofen Medicare 346 26755.72 15.34 OBESITY Paracetamol Aetna 346 26718.69 15.56 ARTHRITIS Penicillin Medicare 369 26690.69 16.56 HYPERTENSION Ibuprofen Aetna 360 26648.9 14.96 CANCER Ibuprofen Medicare 401 26640.84 15.79 DIABETES Paracetamol UnitedHealthcare 341 26636.67 15.7 HYPERTENSION Lipitor Aetna 381 26620.89 15.19 ASTHMA Ibuprofen UnitedHealthcare 401 26553.36 15.08 ARTHRITIS Ibuprofen Blue Cross 349 26530.72 15.95 ARTHRITIS Ibuprofen UnitedHealthcare 351 26526.09 14.72 ASTHMA Lipitor Medicare 396 26440.5 16.21 ARTHRITIS Paracetamol Blue Cross 351 26427.55 15.86 OBESITY Paracetamol Blue Cross 359 26423.81 16.5 ASTHMA Penicillin Aetna 342 26413.85 14.72 ARTHRITIS Aspirin Cigna 373 26404.94 16.13 DIABETES Lipitor Cigna 390 26369.97 14.61 ASTHMA Ibuprofen Cigna 354 26303.22 16.31 ASTHMA Aspirin Medicare 365 26290.47 16.0 HYPERTENSION Lipitor Medicare 319 26276.52 15.88 HYPERTENSION Penicillin Medicare 374 26254.52 15.18 DIABETES Paracetamol Cigna 349 26205.29 15.57 HYPERTENSION Aspirin Medicare 381 26199.26 15.29 OBESITY Aspirin UnitedHealthcare 357 26190.67 15.59 HYPERTENSION Lipitor Blue Cross 352 26176.1 14.14 DIABETES Penicillin Aetna 378 26174.86 16.05 CANCER Ibuprofen Cigna 383 26167.17 15.46 DIABETES Penicillin Cigna 375 26165.0 14.89 OBESITY Penicillin Cigna 356 26134.59 15.65 ASTHMA Penicillin Cigna 403 26134.05 15.72 OBESITY Lipitor Blue Cross 382 26127.51 15.83 DIABETES Lipitor Blue Cross 372 26119.92 15.43 DIABETES Ibuprofen Blue Cross 374 26102.87 15.29 OBESITY Penicillin Aetna 386 26077.22 14.4 DIABETES Penicillin Blue Cross 367 26061.25 15.19 CANCER Paracetamol UnitedHealthcare 365 26059.77 15.03 ASTHMA Aspirin Aetna 360 25997.99 16.3 ARTHRITIS Penicillin Blue Cross 363 25972.24 15.04 OBESITY Lipitor Medicare 361 25945.1 16.19 DIABETES Penicillin UnitedHealthcare 364 25943.43 15.81 ASTHMA Paracetamol UnitedHealthcare 387 25931.71 15.75 OBESITY Paracetamol Medicare 368 25924.75 16.01 ASTHMA Ibuprofen Blue Cross 356 25896.04 16.21 ASTHMA Ibuprofen Aetna 342 25878.82 16.56 DIABETES Paracetamol Medicare 374 25872.72 15.94 HYPERTENSION Penicillin Aetna 362 25806.79 16.22 ARTHRITIS Lipitor Medicare 365 25787.74 15.37 HYPERTENSION Ibuprofen UnitedHealthcare 404 25784.68 15.23 CANCER Penicillin Aetna 363 25734.41 15.51 HYPERTENSION Paracetamol UnitedHealthcare 371 25721.86 15.74 CANCER Paracetamol Medicare 375 25718.51 14.91 ASTHMA Paracetamol Blue Cross 368 25699.36 15.42 OBESITY Lipitor UnitedHealthcare 342 25695.24 15.01 ARTHRITIS Penicillin Aetna 354 25676.0 15.22 OBESITY Ibuprofen UnitedHealthcare 382 25661.12 15.02 ARTHRITIS Paracetamol Aetna 379 25641.1 15.27 CANCER Aspirin Aetna 343 25632.24 16.1 OBESITY Ibuprofen Blue Cross 366 25606.38 15.22 ARTHRITIS Lipitor Blue Cross 361 25558.68 16.23 DIABETES Aspirin Blue Cross 361 25555.35 15.07 ARTHRITIS Aspirin Aetna 377 25553.48 14.55 OBESITY Paracetamol Cigna 348 25539.51 16.45 DIABETES Ibuprofen UnitedHealthcare 355 25532.47 15.05 ASTHMA Lipitor Cigna 356 25505.07 14.92 DIABETES Paracetamol Blue Cross 369 25494.81 15.2 CANCER Paracetamol Cigna 372 25468.15 16.47 ASTHMA Penicillin Blue Cross 369 25450.82 15.38 HYPERTENSION Paracetamol Aetna 387 25446.71 15.05 ARTHRITIS Penicillin Cigna 366 25428.7 15.72 DIABETES Lipitor UnitedHealthcare 369 25422.09 15.54 HYPERTENSION Ibuprofen Medicare 375 25420.04 15.38 CANCER Lipitor Aetna 410 25418.85 14.86 ARTHRITIS Ibuprof

✅ Gold: avg_treatment_costs written!


In [0]:
# ============================================
# CELL 7: Verify Gold Layer
# ============================================
gold_tables = ["readmission_rates", "diagnosis_trends", "avg_treatment_costs"]

for table in gold_tables:
    df = spark.read.parquet(f"{base_path}/gold/hospital_records/{table}/")
    print(f"✅ {table}: {df.count()} rows")

print("\n🎉 All Gold tables verified successfully!")